---
title: "Module 1 Assignment: Corporate Risk Narratives in Form 10-K"
subtitle: "Building a Classical and Neural NLP Pipeline for Industry Analysis"
author:
  - name: Nakul R. Padalkar
    affiliations:
      - id: buu
        name: Boston University
        city: Boston
        state: MA
number-sections: true
date: "2026-02-01"
date-modified: today
date-format: long
engine: jupyter
execute:
  eval: false
  echo: false
---


## Solution Architecture (Mental Model)

```
RAW TXT FILES
     ↓
FILE ITERATION
     ↓
METADATA EXTRACTION (Company, SIC)
     ↓
SECTION EXTRACTION (Item 1A, Item 7)
     ↓
TEXT CLEANING
     ↓
SENTENCE CHUNKING
     ↓
FEATURE REPRESENTATION
     ├── TF-IDF
     └── Neural Embeddings
     ↓
PREDICTIVE MODELS
     ├── Logistic Regression
     └── MLP
     ↓
EVALUATION + FAILURE ANALYSIS
```

This mirrors **enterprise NLP + RAG ingestion**.


## Core Pipeline Code
### Imports & Paths

In [1]:
#| echo: true
#| eval: true

import os
import re
import pandas as pd
import numpy as np
from tqdm import tqdm

from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import classification_report, confusion_matrix

import torch
import torch.nn as nn
from torch.utils.data import DataLoader, TensorDataset

from sentence_transformers import SentenceTransformer

print("PyTorch version:", torch.__version__)
print("CUDA available:", torch.cuda.is_available())

if torch.cuda.is_available():
    print("CUDA version:", torch.version.cuda)
    print("GPU name:", torch.cuda.get_device_name(0))
    print("GPU count:", torch.cuda.device_count())
else:
    print("Running on CPU")

PyTorch version: 2.10.0+cu128
CUDA available: True
CUDA version: 12.8
GPU name: NVIDIA RTX PRO 6000 Blackwell Workstation Edition
GPU count: 1


# Reading Data 

In [2]:
DATA_DIR = "../../data/SEC-10K-2024"

all_files = sorted([
    f for f in os.listdir(DATA_DIR)
    if f.lower().endswith(".txt")
])

print(f"Total files available: {len(all_files)}")

Total files available: 7754


### Get small set

In [3]:
#| echo: true
#| eval: true

MAX_FILES = 100  # instructor fast mode

selected_files = all_files[:MAX_FILES]

print(f"Processing {len(selected_files)} files")

Processing 100 files


### Get English Stopwords

In [4]:
#| echo: true
#| eval: true
import nltk
from nltk.corpus import stopwords

nltk.download("stopwords")
nltk.download("punkt")

STOP_WORDS = list(set(stopwords.words("english")))

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\nakul\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\nakul\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


## Load & Parse All 10-K Files
### Extract SIC Code

In [5]:
#| echo: true
#| eval: true
#| 
def extract_sic(text):
    match = re.search(r"SIC\s*:\s*(\d{4})", text)
    return match.group(1) if match else None

### Extract Sections (Robust, Regex-Based)

In [6]:
#| echo: true
#| eval: true
def extract_section(text, start_pattern, end_pattern):
    start = re.search(start_pattern, text, re.IGNORECASE)
    end = re.search(end_pattern, text, re.IGNORECASE)
    if start and end and start.start() < end.start():
        return text[start.end():end.start()].strip()
    return ""

### Parse All Files

In [7]:
#| echo: true
#| eval: true

records = []

for fname in selected_files:
    path = os.path.join(DATA_DIR, fname)

    try:
        with open(path, "r", encoding="utf-8", errors="ignore") as f:
            text = f.read()

        records.append({
            "file": fname,
            "raw_text": text
        })

    except Exception as e:
        records.append({
            "file": fname,
            "raw_text": "",
            "ingest_error": str(e)
        })

df = pd.DataFrame(records)
print(f"Files ingested: {len(df)}")
# df hide index head

df.head(2).style.hide(axis='index')

Files ingested: 100


## Clean & Sentence-Chunk Text
You will run in to a problem here. Since we are "cleaning" the text it could result in removing special identifiers and symbols. This will result in the removal of the XBRL/IXBRL tags. Can you think of a solution for this?

In [8]:
# import re

# def remove_xbrl_header(text):
#     return re.sub(
#         r"<Header>.*?</Header>",
#         "",
#         text,
#         flags=re.DOTALL | re.IGNORECASE
#     )
    
# df["text_no_header"] = df["raw_text"].apply(remove_xbrl_header)


In [9]:
import re

def remove_sec_preamble(text):
    pattern = r"UNITED STATES\s+SECURITIES AND EXCHANGE COMMISSION"
    match = re.search(pattern, text, flags=re.IGNORECASE)
    
    if match:
        return text[match.start():]
    else:
        return text  # fallback: return original if phrase not found
df["text_no_preamble"] = df["raw_text"].apply(remove_sec_preamble)

In [10]:
#| echo: true
#| eval: true
def clean_text(text):
    text = re.sub(r"\s+", " ", text)
    text = re.sub(r"[^A-Za-z0-9\.,;:\-\(\)\s]", "", text)
    return text.strip()

df["raw_clean"] = df["text_no_preamble"].apply(clean_text)
df.head(2).style.hide(axis='index')

Sentence chunking (simple, explainable):

In [11]:
#| echo: true
#| eval: true
def sentence_split(text):
    return re.split(r"(?<=[.!?])\s+", text)

df["raw_sentences"] = df["raw_clean"].apply(sentence_split)
df.head(2).style.hide(axis='index')

## Feature Engineering

### Cleaning Empty Entries

In [12]:
#| echo: true
#| eval: true

# Minimum length threshold (characters)
MIN_LEN = 300  

df["raw_len"] = df["raw_clean"].str.len()

bad_docs = df[df["raw_len"] < MIN_LEN]
good_docs = df[df["raw_len"] >= MIN_LEN]

print(f"Documents dropped: {len(bad_docs)}")
print(f"Documents kept: {len(good_docs)}")

Documents dropped: 0
Documents kept: 100


### SEC SIC Codes Extraction

In [13]:
#| echo: true
#| eval: true
import re

def extract_sic_code(text: str) -> str | None:
    """
    Extracts the 4-digit SIC code from SEC 10-K text.
    Returns None if not found.
    """
    patterns = [
        r"SIC\s*:\s*(\d{4})",
        r"STANDARD\s+INDUSTRIAL\s+CLASSIFICATION\s*[:\-]?\s*(?:[^\[]+)?\[(\d{4})\]",
        r"STANDARD\s+INDUSTRIAL\s+CLASSIFICATION\s*[:\-]?\s*(\d{4})"
    ]

    for pat in patterns:
        match = re.search(pat, text, re.IGNORECASE)
        if match:
            return match.group(1)

    return None

good_docs["sic_code"] = good_docs["raw_text"].apply(extract_sic_code)

### Firm Name 

In [14]:
#| echo: true
#| eval: true

def extract_company_name(text: str) -> str | None:
    """
    Attempts to extract company name from header section.
    Heuristic-based; may fail silently.
    """
    match = re.search(
        r"COMPANY\s+CONFORMED\s+NAME\s*:\s*(.+)",
        text,
        re.IGNORECASE
    )
    return match.group(1).strip() if match else None

### Item Extraction

In [15]:
#| echo: true
#| eval: true

def extract_item_section(
    text: str,
    item_number: str,
    next_item_number: str
) -> str:
    """
    Extracts text between ITEM <item_number> and ITEM <next_item_number>.
    Returns empty string if extraction fails.
    """
    try:
        start_pattern = rf"ITEM\s+{item_number}\.?\s+"
        end_pattern = rf"ITEM\s+{next_item_number}\.?\s+"

        start_match = re.search(start_pattern, text, re.IGNORECASE)
        end_match = re.search(end_pattern, text, re.IGNORECASE)

        if not start_match or not end_match:
            return ""

        if start_match.start() >= end_match.start():
            return ""

        return text[start_match.end():end_match.start()].strip()

    except Exception:
        return ""

def extract_item_1a(text: str) -> str:
    return extract_item_section(text, "1A", "1B")

def extract_item_7(text: str) -> str:
    return extract_item_section(text, "7", "7A")

### Extracting Information

In [16]:
#| echo: true
#| eval: true


df["sic"] = df["raw_text"].apply(extract_sic_code)
df["company"] = df["raw_text"].apply(extract_company_name)

df["risk_text"] = df["raw_text"].apply(extract_item_1a)
df["mdna_text"] = df["raw_text"].apply(extract_item_7)

df.head(2).style.hide(axis='index')

### Log errored files

In [17]:
#| echo: true
#| eval: false

error_log = bad_docs[["file", "sic", "raw_len"]]
error_log.to_csv("tfidf_dropped_files.csv", index=False)

error_log.head()

KeyError: "['sic'] not in index"

### TF-IDF (Classical NLP)

In [ ]:
#| echo: true
#| eval: false
#| 
vectorizer = TfidfVectorizer(
    stop_words=STOP_WORDS,   # list or "english"
    min_df=2,
    max_df=0.95,
    ngram_range=(1, 2),
    token_pattern=r"(?u)\b[a-zA-Z][a-zA-Z]+\b"
)

X_tfidf = vectorizer.fit_transform(good_docs["raw_clean"])
y = good_docs["sic"]

### Neural Embeddings (Instructor Baseline)

In [ ]:
#| echo: true
#| eval: true
embedder = SentenceTransformer("all-MiniLM-L6-v2")

X_embed = embedder.encode(
    good_docs["raw_clean"].tolist(),
    show_progress_bar=True
)

## Predictive Modeling (Q3 Solution)

### Train/Test Split

In [ ]:
#| echo: true
#| eval: false
X_train, X_test, y_train, y_test = train_test_split(
    X_tfidf, y, test_size=0.2, random_state=42, stratify=y
)

### Model A: Logistic Regression (TF-IDF)

In [ ]:
#| echo: true
#| eval: false
#| 

clf = LogisticRegression(max_iter=1000)
clf.fit(X_train, y_train)

y_pred = clf.predict(X_test)

print(classification_report(y_test, y_pred))

---

### Model B: Neural MLP (Embeddings)

In [ ]:
#| echo: true
#| eval: false
class MLP(nn.Module):
    def __init__(self, input_dim, num_classes):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(input_dim, 256),
            nn.ReLU(),
            nn.Linear(256, num_classes)
        )
    def forward(self, x):
        return self.net(x)

In [ ]:
#| echo: true
#| eval: false
label_map = {k: i for i, k in enumerate(sorted(df["sic"].unique()))}
inv_label_map = {v: k for k, v in label_map.items()}

y_num = df["sic"].map(label_map).values

In [ ]:
#| echo: true
#| eval: false
X_train, X_test, y_train, y_test = train_test_split(
    X_embed, y_num, test_size=0.2, random_state=42
)

train_ds = TensorDataset(
    torch.tensor(X_train, dtype=torch.float32),
    torch.tensor(y_train, dtype=torch.long)
)

train_dl = DataLoader(train_ds, batch_size=32, shuffle=True)

In [ ]:
#| echo: true
#| eval: false
model = MLP(X_embed.shape[1], len(label_map))
opt = torch.optim.Adam(model.parameters(), lr=1e-3)
loss_fn = nn.CrossEntropyLoss()

for epoch in range(5):
    for xb, yb in train_dl:
        opt.zero_grad()
        loss = loss_fn(model(xb), yb)
        loss.backward()
        opt.step()

## Error Analysis (Q4 Solution)

In [ ]:
#| echo: true
#| eval: false
conf = confusion_matrix(y_test, y_pred)
conf

Manual inspection helper:

In [ ]:
#| echo: true
#| eval: false
mis_idx = np.where(y_test != y_pred)[0]

df.iloc[mis_idx][["file", "sic", "risk_clean"]].head(3)

## Artifacts to Preserve for Assignments 2–5

You should **save these once**:

In [ ]:
df.to_pickle("processed_corpus.pkl")
np.save("risk_embeddings.npy", X_embed)

These will directly feed:

* vector search
* RAG pipelines
* LLM retrieval filters
* evaluation benchmarks